In [45]:
import json
from tqdm import tqdm_notebook

import dash
import dash_html_components as html
import dash_core_components as dcc
import dash_bootstrap_components as dbc
import plotly.graph_objs as go
from dash.dependencies import Input, Output, State
import numpy as np
import pandas as pd
import plotly.express as px

## Correcting the Merged Plot GeoJSON

In [46]:
with open(r'E:\RBS_Projects\dehradunDIS\data_staging_area\plots.geojson') as f:
    znew = json.load(f)
    
df = pd.read_csv('E:\RBS_Projects\dehradunDIS\data_staging_area\merged_plots_dis.csv')

In [39]:
features_list = []

for x in tqdm_notebook(znew['features']):
    
    geometry_dict = x['geometry']
    
    geometry_dict['type'] = 'Polygon'
    
    if(len(geometry_dict['coordinates']) > 0):
        geometry_dict['coordinates'] = geometry_dict['coordinates'][0]

        dict_to_be_appended = {'type': 'Feature', 'properties': x['properties'], 
                               'geometry': geometry_dict, 'id': x['properties']['UID']}

        features_list.append(dict_to_be_appended)

<ipython-input-39-3814411c7a87>:3: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  for x in tqdm_notebook(znew['features']):


  0%|          | 0/4412 [00:00<?, ?it/s]

In [40]:
znew_arranged = {'type': 'FeatureCollection', 'features': features_list}

In [42]:
with open("data_staging_area\plots_corrected_for_dash.geojson", "w") as outfile:  
    json.dump(znew_arranged, outfile) 

## Testing Maps

In [49]:
fig = px.choropleth_mapbox(df, geojson=znew_arranged, locations='UID', 
                           color_continuous_scale="Viridis",
                           
                          )



fig.update_layout(
    mapbox_style="white-bg",
    mapbox_layers=[
        {
            "below": 'traces',
            "sourcetype": "raster",
            "sourceattribution": "Google, RBS Pvt. Ltd.",
            "source": [
                "http://mt0.google.com/vt/lyrs=s&hl=en&x={x}&y={y}&z={z}"
            ]
        }
      ])

fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.update(layout_showlegend=False)